In [5]:
import torch
from transformers import AutoProcessor, AutoModelForVision2Seq, TrainingArguments, Trainer
from peft import LoraConfig, get_peft_model
from PIL import Image
import pandas as pd
import os

ValueError: Your currently installed version of Keras is Keras 3, but this is not yet supported in Transformers. Please install the backwards-compatible tf-keras package with `pip install tf-keras`.

In [ ]:
# === 1. Подготовка данных ===
df = pd.read_csv("plantdoc_annotation.csv", sep=';').drop('Unnamed: 2', axis=1)
df['image_path'] = df['id'].apply(lambda x: 'plantsdoc/' + x)
df['label'] = df['classes'].apply(lambda x: eval(x))

dataset = load_dataset(
    "imagefolder",
    data_dir="images",
    split="train"
)

# Альтернатива: напрямую из CSV
# from datasets import Dataset
# dataset = Dataset.from_pandas(df)

In [ ]:
# === 2. Модель и процессор ===
model_id = "Salesforce/blip2-flan-t5-base"
processor = AutoProcessor.from_pretrained(model_id)
model = AutoModelForVision2Seq.from_pretrained(
    model_id,
    load_in_8bit=True,
    device_map="auto"
)

In [ ]:
# === 3. Добавляем LoRA ===
lora_config = LoraConfig(
    r=8,
    lora_alpha=16,
    target_modules=["q_proj", "v_proj"],
    lora_dropout=0.1,
    bias="none",
    task_type="SEQ_2_SEQ_LM"
)
model = get_peft_model(model, lora_config)

In [ ]:
# === 4. Препроцессинг данных ===
def preprocess(example):
    image = Image.open(example["image_path"]).convert("RGB")
    inputs = processor(
        images=image,
        text=example["label"],
        return_tensors="pt",
        padding="max_length",
        truncation=True
    )
    inputs["labels"] = inputs["input_ids"]
    return {k: v.squeeze() for k, v in inputs.items()}

dataset = dataset.map(preprocess)

In [ ]:
# === 5. Параметры обучения ===
training_args = TrainingArguments(
    output_dir="./blip2_finetuned",
    per_device_train_batch_size=2,
    gradient_accumulation_steps=8,
    learning_rate=1e-4,
    num_train_epochs=5,
    logging_dir="./logs",
    fp16=True,
    save_steps=500,
    save_total_limit=1,
    report_to="none"
)

In [ ]:
# === 6. Тренировка ===
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=dataset,
)

trainer.train()

# === 7. Сохранение модели ===
trainer.save_model("blip2_plant_finetuned")